In [1]:
!pip install openai==0.28

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.5/76.5 kB 3.9 MB/s eta 0:00:00
  Attempting uninstall: openai
    Found existing installation: openai 1.59.9
    Uninstalling openai-1.59.9:
      Successfully uninstalled openai-1.59.9


In [2]:
!pip install pdf2image
!sudo apt-get install poppler-utils


Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following NEW packages will be installed:
  poppler-utils
0 upgraded, 1 newly installed, 0 to remove and 18 not upgraded.
Need to get 186 kB of archives.
After this operation, 696 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy-updates/main amd64 poppler-utils amd64 22.02.0-2ubuntu0.6 [186 kB]
Fetched 186 kB in 1s (260 kB/s)
debconf: unable to initialize frontend: Dialog
debconf: (No usable dialog-like program is installed, so the dialog based frontend cannot be used. at /usr/share/perl5/Debconf/FrontEnd/Dialog.pm line 78, <> line 1.)
debconf: falling back to frontend: Readline
debconf: unable to initialize frontend: Readline
debconf: (This frontend requires a controlling tty.)
debconf: falling back to frontend: Teletype
dpkg-preconfigure: unable to re-open stdin: 
Selecting previously unselected package poppler-utils.
(Reading database ... 124950 

In [4]:
import openai
from pdf2image import convert_from_path
import json
import pandas as pd
import os
import base64
import re

# OpenAI API Key
openai.api_key = "key"

# Set Paths
pdf_path = "/content/QB-MARATHI.pdf"
source = "https://transport.maharashtra.gov.in/Site/Upload/Pdf/QB-MARATHI.pdf"
results_folder = "/content/results"
images_folder = os.path.join(results_folder, "images")
os.makedirs(results_folder, exist_ok=True)
os.makedirs(images_folder, exist_ok=True)

# GPT Prompt
pre_prompt = """Please extract the multiple-choice questions in the attached image in Marathi.
There can be one or multiple questions per page.

Format the output as:
<question_num>Question Number</question_num>
<question>Question Text</question>
<choices>
    <choice>A</choice>
    <choice>B</choice>
    <choice>C</choice>
</choices>
<answer>Correct Answer Index (1, 2, or 3)</answer>
<image>yes/no</image>

IMPORTANT:
- The <answer> tag should contain ONLY a single integer: 1, 2, or 3.
- Do NOT include the actual answer text, only the index.
- If no answer is available, leave <answer></answer> empty.
- If the question has an associated image (diagram, symbol, road sign), respond with `<image>yes</image>`.
- Otherwise, respond with `<image>no</image>`.
- If the image contains a reference like 'चित्रात दाखवल्याप्रमाणे' (Marathi for "as shown in the figure"), ensure `<image>yes</image>`.
- Ensure options are unique and contain at least two valid choices.
"""

# Convert PDF to Images
def convert_pdf_to_images(pdf_path):
    print("📄 Converting PDF to Images...")
    images = convert_from_path(pdf_path, dpi=300)
    image_paths = []

    for i, image in enumerate(images):
        img_path = os.path.join(images_folder, f"page_{i+1}.png")
        image.save(img_path, "PNG")
        image_paths.append(img_path)

    print(f"✅ {len(image_paths)} images saved.")
    return image_paths

# Encode Image in Base64
def encode_image(image_path):
    with open(image_path, "rb") as image_file:
        return base64.b64encode(image_file.read()).decode("utf-8")

# Process Image with GPT-4o
def gpt4o_process_image(image_path):
    base64_image = encode_image(image_path)

    try:
        response = openai.ChatCompletion.create(
            model="gpt-4o",
            messages=[
                {"role": "system", "content": pre_prompt},
                {"role": "user", "content": [
                    {"type": "text", "text": "Extract all questions from this image."},
                    {"type": "image_url", "image_url": {"url": f"data:image/png;base64,{base64_image}"}}
                ]}
            ],
            max_tokens=2000
        )

        extracted_text = response["choices"][0]["message"]["content"]
        return extracted_text

    except json.JSONDecodeError:
        print("❌ Error: GPT-4o returned an invalid JSON format.")
        return None

# Parse GPT Response & Fix Issues
def parse_gpt_output(response):
    # Regex patterns for structured extraction
    q_num_pattern = re.compile(r"<question_num>(\d+)</question_num>")
    q_pattern = re.compile(r"<question>(.*?)</question>")
    choices_pattern = re.compile(r"<choices>(.*?)</choices>", re.DOTALL)
    answer_pattern = re.compile(r"<answer>(.*?)</answer>")
    image_pattern = re.compile(r"<image>(.*?)</image>")

    # Extract values
    question_nums = q_num_pattern.findall(response)
    questions = q_pattern.findall(response)
    choices_raw = choices_pattern.findall(response)
    answers_raw = answer_pattern.findall(response)
    images_required = image_pattern.findall(response)

    # Extract choices correctly & ensure uniqueness
    choices = []
    for choice_text in choices_raw:
        extracted_choices = list(set(re.findall(r"<choice>(.*?)</choice>", choice_text)))  # Ensure unique choices
        if len(extracted_choices) < 2:  # Validator requires at least two options
            extracted_choices.append("Option Placeholder")  # Add dummy placeholder
        choices.append(extracted_choices)

    # Convert to integer (1,2,3) and validate range
    valid_answers = []
    for answer in answers_raw:
        try:
            int_answer = int(answer.strip())
            if 1 <= int_answer <= 3:  # Ensure valid 1-based index
                valid_answers.append(int_answer)
            else:
                valid_answers.append(None)
        except ValueError:
            valid_answers.append(None)

    # Ensure all lists have the same length
    min_length = min(len(question_nums), len(questions), len(choices), len(valid_answers), len(images_required))
    question_nums = question_nums[:min_length]
    questions = questions[:min_length]
    choices = choices[:min_length]
    valid_answers = valid_answers[:min_length]
    images_required = images_required[:min_length]

    return question_nums, questions, choices, valid_answers, images_required

# Main Execution
def main():
    image_paths = convert_pdf_to_images(pdf_path)
    all_questions = []

    for img_path in image_paths:
        print(f"📷 Processing {img_path}...")
        response = gpt4o_process_image(img_path)

        if response:
            q_nums, q_texts, options, correct_answers, images_required = parse_gpt_output(response)

            for i in range(len(q_nums)):
                image_info = None
                image_png = None
                image_type = None

                if images_required[i] == "yes":
                    image_png = f"driving-license-marathi-{q_nums[i]}.png"
                    image_info = "essential"
                    image_type = "diagram"

                question_data = {
                    "language": "mr",
                    "country": "India",
                    "file_name": "QB-MARATHI.pdf",
                    "source": source,
                    "license": "Education and Research",
                    "level": "Driver License",
                    "category_en": "Driving",
                    "category_original_lang": "ड्रायव्हिंग",
                    "original_question_num": int(q_nums[i]),
                    "question": q_texts[i],
                    "options": options[i] if i < len(options) else [],
                    "answer": correct_answers[i],  # ✅ Always 1,2,3
                    "image_png": image_png,
                    "image_information": image_info,
                    "image_type": image_type,
                    "parallel_question_id": None
                }
                all_questions.append(question_data)

    # Save as JSON
    json_path = os.path.join(results_folder, "marathi_driving_license_valid.json")
    with open(json_path, "w", encoding="utf-8") as f:
        json.dump(all_questions, f, indent=4, ensure_ascii=False)

    # Convert to CSV
    df = pd.DataFrame(all_questions)
    csv_path = os.path.join(results_folder, "marathi_driving_license_valid.csv")
    df.to_csv(csv_path, index=False, encoding="utf-8")

    print(f"✅ JSON Saved: {json_path}")
    print(f"✅ CSV Saved: {csv_path}")

# Run the script
main()


📄 Converting PDF to Images...
✅ 107 images saved.
📷 Processing /content/results/images/page_1.png...
📷 Processing /content/results/images/page_2.png...
📷 Processing /content/results/images/page_3.png...
📷 Processing /content/results/images/page_4.png...
📷 Processing /content/results/images/page_5.png...
📷 Processing /content/results/images/page_6.png...
📷 Processing /content/results/images/page_7.png...
📷 Processing /content/results/images/page_8.png...
📷 Processing /content/results/images/page_9.png...
📷 Processing /content/results/images/page_10.png...
📷 Processing /content/results/images/page_11.png...
📷 Processing /content/results/images/page_12.png...
📷 Processing /content/results/images/page_13.png...
📷 Processing /content/results/images/page_14.png...
📷 Processing /content/results/images/page_15.png...
📷 Processing /content/results/images/page_16.png...
📷 Processing /content/results/images/page_17.png...
📷 Processing /content/results/images/page_18.png...
📷 Processing /content/r